In [ ]:
![ -f root_v6.32.10.Linux-ubuntu22.04-x86_64-gcc11.4.tar.gz ] || wget https://root.cern/download/root_v6.32.10.Linux-ubuntu22.04-x86_64-gcc11.4.tar.gz
!tar -xzf root_v6.32.10.Linux-ubuntu22.04-x86_64-gcc11.4.tar.gz

In [ ]:
#Getting all the dependencies needed to run ROOT in colabs
#In case the notebook crashes, only need to rerun this block
!sudo apt-get install dpkg-dev cmake g++ gcc binutils libx11-dev libxpm-dev libxft-dev libxext-dev python3 libssl-dev libafterimage0
import sys
sys.path.append("/content/root/lib")
import ctypes
ctypes.cdll.LoadLibrary('/content/root/lib/libCore.so')
ctypes.cdll.LoadLibrary('/content/root/lib/libThread.so')
ctypes.cdll.LoadLibrary('/content/root/lib/libImt.so')
ctypes.cdll.LoadLibrary('/content/root/lib/libRIO.so')
ctypes.cdll.LoadLibrary('/content/root/lib/libNet.so')
ctypes.cdll.LoadLibrary('/content/root/lib/libTree.so')
ctypes.cdll.LoadLibrary('/content/root/lib/libMathCore.so')
ctypes.cdll.LoadLibrary('/content/root/lib/libMatrix.so')
ctypes.cdll.LoadLibrary('/content/root/lib/libHist.so')
ctypes.cdll.LoadLibrary('/content/root/lib/libGraf.so')

In [ ]:
#Checking whether ROOT is functioning properly (do this everytime to also import ROOT)
!python --version
import ROOT
h = ROOT.TH1F("gauss","Example histogram",100,-4,4)
h.FillRandom("gaus")
c = ROOT.TCanvas("myCanvasName","The Canvas Title",800,600)
h.Draw()
c.Draw()

In [5]:
#Block to import all the ROOT functions that we will be using throughout this template
from ROOT import TFile
from ROOT import TLorentzVector
from ROOT import TH1F
import numpy as np
from ROOT import RooRealVar
from ROOT import RooDataHist
from ROOT import RooDataSet
from ROOT import RooExponential
from ROOT import RooGaussian
from ROOT import RooArgList
from ROOT import RooArgSet
from ROOT import RooAddPdf
from ROOT import RooPlot
from ROOT import TLegend
from ROOT import RooFit
from ROOT import TLatex
from ROOT import RooChi2Var
from ROOT import RooAbsData

In [ ]:
#Getting data file (to be run only once)

# option 1: copy it directly in the workspace (faster if you run this program only today)
!wget https://aboletti.web.cern.ch/aboletti/LIP-tutorial/Skim4.root
f1 = TFile("Skim4.root")

## option 2: download file from previous link to your PC, then upload it to your google drive, as "My Drive/Colab Notebooks/data/Skim4.root" (better if you will run this code in multiple sessions)
#from google.colab import drive
#drive.mount('/content/gdrive')
#f1 = TFile("/content/gdrive/My Drive/Colab Notebooks/data/Skim4.root")

In [ ]:
#Simple command to check the contents on the .root file (to be run only once)

f1.ls()

#oniaTree is the TTree in the Skim4.root file, as shown by the previous command
f1.oniaTree.Print()

In [8]:
#Establishing the canvas so we can draw the plots
c = ROOT.TCanvas("c","",800,600)

In [ ]:
# Plotting a simple histogram with the Dimuons' mass

hist1 = TH1F("Mass","hDimuonMass_normal",500, 0, 200)

#Iterating over events in order to fill the histogram with the dimuon invariant mass
maxEvents = f1["oniaTree"].GetEntries()

for index, event in enumerate(f1["oniaTree"]):
  hist1.Fill(event.dimuon_p4.M())
  if index > maxEvents:break

#Drawing the histogram, in the previously created canvas, with logarithmic axes
hist1.Draw()
c.SetLogy(False)
c.SetLogx(False)
c.Draw()

#Exercise: adapt axes' properties to improve the visualization of the spectrum

In [ ]:
# Plotting the Dimuon's mass in an histogram with variable bin widths

#Creating an array with values corresponding to each bin's width
maxbins = 100000
xbins = [0]*maxbins
xbins[0] = 0.1
nbins = 0
binproportion = 0.005
i = 1
while xbins[nbins]<500:
  xbins[i] = xbins[i-1]*(1+binproportion)
  nbins += 1
  i += 1
  if nbins >= maxbins: break
#xbins needs to be converted into an array (we have been using lists) because
# TH1F takes an array as input
xbinsarray = np.array(xbins)


hist2 = TH1F("Mass_Log","hDimuonMass_normal", nbins, xbinsarray)

#Iterating over all events to fill the histogram
maxEvents = f1.oniaTree.GetEntries()

for index, event in enumerate(f1.oniaTree):
  hist2.Fill(event.dimuon_p4.M())
  if index > maxEvents:break

#Drawing the histogram
hist2.Draw()
c.SetLogy(True)
c.SetLogx(True)
c.Draw()

In [ ]:
# Fitting the J/Psi peak

#Setting the mass limits of the peak
mmin = 2.9
mmax = 3.3

hist3 = TH1F("Mass","hDimuonMass_peak",100, mmin, mmax)

#Filling the histogram with the relevant data
maxEvents = f1.oniaTree.GetEntries()

for index, event in enumerate(f1.oniaTree):
  hist3.Fill(event.dimuon_p4.M())
  if index > maxEvents: break

#Create a Mass variable that RooFit can use, and importing the relevant dataset
mass = RooRealVar("mass", "#mu^{+}#mu^{-} invariant mass", mmin, mmax, "GeV/c^{2}")
args = RooArgList(mass)
dh = RooDataHist("dh", "dh", args, hist3)

#Define background model (exponential) and its parameters
Lambda = RooRealVar("lambda", "lambda", -0.3, -4.0, 0.0)
background = RooExponential("background", "background", mass, Lambda)

#Define signal model (Gaussian) and its parameters
mean = RooRealVar("mean", "mean", 0.5*(mmin+mmax), mmin, mmax)
sigma = RooRealVar("sigma", "sigma", 0.1*(mmax-mmin),0.,0.5*(mmax-mmin))
signal = RooGaussian("signal", "signal", mass, mean, sigma)

#Define variables for number of signal and background events
n_signal_initial = 0.8*dh.sumEntries()
n_back_initial = 0.2*dh.sumEntries()
n_signal = RooRealVar("n_signal","n_signal",n_signal_initial,0.,dh.sumEntries())
n_back = RooRealVar("n_back","n_back",n_back_initial,0.,dh.sumEntries())

#Sum signal and background models
model = RooAddPdf("model", "model", RooArgList(signal, background), RooArgList(n_signal, n_back))

#Perform the fit
model.fitTo(dh)

#Plot7 the fit
frame = mass.frame()
frame.SetTitle("#mu^{+}#mu^{-} mass spectrum")

dh.plotOn(frame,RooFit.Name("dh"))
model.plotOn(frame,RooFit.Name("modelSig"),RooFit.Components("signal"),RooFit.LineStyle(ROOT.kDashed))
model.plotOn(frame,RooFit.Name("modelBkg"),RooFit.Components("background"),RooFit.LineStyle(ROOT.kDashed),RooFit.LineColor(ROOT.kRed))
model.plotOn(frame,RooFit.Name("model"))

roofit_canvas = ROOT.TCanvas()
frame.Draw()

#Draw a caption
legend = TLegend(0.65,0.6,0.88,0.85)
legend.SetBorderSize(0)
legend.SetTextFont(40)
legend.SetTextSize(0.04)
legend.AddEntry(frame.findObject("dh"),"Data","1pe")
legend.AddEntry(frame.findObject("modelBkg"),"Background fit","1pe")
legend.AddEntry(frame.findObject("modelSig"),"Signal fit","1pe")
legend.AddEntry(frame.findObject("model"),"Global fit","1pe")
legend.Draw()

#Display info and fit results
L = TLatex()
L.SetNDC()
L.SetTextSize(0.04)
L.DrawLatex(0.15,0.8,"Dimuon Spectrum")
L.SetTextSize(0.03)
L.DrawLatex(0.15,0.75,"ressonance: J/#psi")
L.DrawLatex(0.15,0.70,ROOT.Form("mass: %5.3f #pm %5.3f GeV/c^{2}" % (mean.getVal(),mean.getError())))
L.DrawLatex(0.15,0.65,ROOT.Form("with #sigma: %5.3f #pm %5.3f MeV/c^{2}" % (sigma.getVal()*1000,sigma.getError()*1000)))
L.DrawLatex(0.15,0.60,ROOT.Form("yield: %.0f #pm %.0f events" % (n_signal.getVal(),n_signal.getError())))
chi = RooChi2Var("chi","chi^2",model,dh,True,RooAbsData.Poisson)
variables = 5 # This is the number of free parameters in our model, and the
              # number of degrees of freedom is the the number of points in our
              # model minus the free parameters
L.DrawLatex(0.15,0.55,ROOT.Form("#chi^{2}/ndf from the RooChi2Var"))
L.DrawLatex(0.15,0.50,ROOT.Form("for %i ndf.: %.2f" % (variables,(chi.getVal()/(100.-variables)))))
L.DrawLatex(0.15,0.45,ROOT.Form("#chi^{2}/ndf from the frame method"))
L.DrawLatex(0.15,0.40,ROOT.Form("for %i ndf.: %.2f" %  (variables,frame.chiSquare(variables))))

roofit_canvas.Draw()

In [ ]:
#Making an unbinned Fit
#The main difference is that instead of feeding the model a RooDataHist
#we feed it a RooDataSet object

#Setting the mass limits of the peak
mmin = 2.9
mmax = 3.3

#Performing the mass cut a priori
#There are several ways of initiating a RooDataSet object
#One of them is by directly importing a TTree object
#If we do so, then we must define every variable in the TTree as a RooRealVar
#And we can perform the cuts directly on the RooDataSet when initiating it
#or afterwards with RooCut objects
masslist = []
for entry in f1.oniaTree:
  if mmin <= entry.dimuon_p4.M() <= mmax:
    masslist.append(entry.dimuon_p4.M())

#Create a Mass variable that RooFit can use, and importing the relevant dataset
mass = RooRealVar("mass", "#mu^{+}#mu^{-} invariant mass", mmin, mmax, "GeV/c^{2}")
ds = RooDataSet("ds","ds",RooArgSet(mass))

#We will set the entries one by one on the RooDataSet. This can be generalized
#for n dimensions with setValue() for each variable
#followed by ds.add(RooArgSet(mass, var0, var1, ..., varn))
for value in masslist:
  mass.setVal(value)
  ds.add(RooArgSet(mass))

#Simple way of checking the RooDataSet entries if you want to make sure that
#the RooDataSet has been correctly filled
for n in range(9):
  ds.get(n).Print("v")

#Define background model (exponential) and its parameters I chose this because everythign in particle physics are exponentials
Lambda = RooRealVar("lambda", "lambda", -0.3, -4.0, 0.0)
background = RooExponential("background", "background", mass, Lambda)

#Define signal model (Gaussian) and its parameters
mean = RooRealVar("mean", "mean", 0.5*(mmin+mmax), mmin, mmax)
sigma = RooRealVar("sigma", "sigma", 0.1*(mmax-mmin),0.,0.5*(mmax-mmin))
signal = RooGaussian("signal", "signal", mass, mean, sigma)

#Define variables for number of signal and background events
n_signal_initial = 0.8*ds.sumEntries()
n_back_initial = 0.2*ds.sumEntries()
n_signal = RooRealVar("n_signal","n_signal",n_signal_initial,0.,ds.sumEntries())
n_back = RooRealVar("n_back","n_back",n_back_initial,0.,ds.sumEntries())

#Sum signal and background models
model = RooAddPdf("model", "model", RooArgList(signal, background), RooArgList(n_signal, n_back))

#Perform the fit
model.fitTo(ds)

#Plot the fit
frame = mass.frame()
frame.SetTitle("#mu^{+}#mu^{-} mass spectrum with exponential and Gauss")

ds.plotOn(frame,RooFit.Name("ds"))
model.plotOn(frame,RooFit.Name("modelSig"),RooFit.Components("signal"),RooFit.LineStyle(ROOT.kDashed))
model.plotOn(frame,RooFit.Name("modelBkg"),RooFit.Components("background"),RooFit.LineStyle(ROOT.kDashed),RooFit.LineColor(ROOT.kRed))
model.plotOn(frame,RooFit.Name("model"))

roofit_canvas = ROOT.TCanvas()
frame.Draw()

#Draw a caption
legend = TLegend(0.65,0.6,0.88,0.85)
legend.SetBorderSize(0)
legend.SetTextFont(40)
legend.SetTextSize(0.04)
legend.AddEntry(frame.findObject("ds"),"Data","1pe")
legend.AddEntry(frame.findObject("modelBkg"),"Background fit","1pe")
legend.AddEntry(frame.findObject("modelSig"),"Signal fit","1pe")
legend.AddEntry(frame.findObject("model"),"Global fit","1pe")
legend.Draw()

#Display info and fit results
L = TLatex()
L.SetNDC()
L.SetTextSize(0.04)
L.DrawLatex(0.15,0.8,"Dimuon Spectrum")
L.SetTextSize(0.03)
L.DrawLatex(0.15,0.75,"ressonance: J/#psi")
L.DrawLatex(0.15,0.70,ROOT.Form("mass: %5.3f #pm %5.3f GeV/c^{2}" % (mean.getVal(),mean.getError())))
L.DrawLatex(0.15,0.65,ROOT.Form("with sigma: %5.3f #pm %5.3f MeV/c^{2}" % (sigma.getVal()*1000,sigma.getError()*1000)))
L.DrawLatex(0.15,0.60,ROOT.Form("yield: %.0f #pm %.0f events" % (n_signal.getVal(),n_signal.getError())))
free_parameters = 5
L.DrawLatex(0.15,0.55,ROOT.Form("#chi^{2} from the frame method"))
L.DrawLatex(0.15,0.50,ROOT.Form("for 5 d.o.f.: %.2f" % frame.chiSquare(free_parameters)))

roofit_canvas.Draw()
